In [1]:
import os 
test_files = [os.path.join('test_files', f) for f in sorted(os.listdir('test_files'))]
print(test_files)

['test_files/YeMi.dna', 'test_files/YeMi.dna.lz4', 'test_files/aes.tar', 'test_files/aes.tar.lz4', 'test_files/file26.bmp', 'test_files/file26.bmp.lz4', 'test_files/file28.bmp', 'test_files/file28.bmp.lz4', 'test_files/openssl', 'test_files/openssl.lz4', 'test_files/wells_the_invisible_man.txt', 'test_files/wells_the_invisible_man.txt.lz4']


In this example we have 0x12 where 1 represents the length of the a literal and 2 represents the number to copy from another buffer


Decode the following sequence 

\x12\x00\x00\x00\x10a\x01\x00\x10 \x05\x00\x0f\x02\x00SPaaaaa'



0x10 => Token  
a => literal 
0x01 => offset => little edian = 1 = current position 
0x00 => offset 
0x10 => Token
space character => literal  
0x05 => offset = 5
0x00 => offset 
0x0F => token (no literal, 4 high bits = 0), match length is > 15   
0x02 => offset = 2 
0x00 => offset 
0x53 = S => 83 + 15 = 98 = match length 
0x50 = P => token 
a => literal 1
a => literal 2prueba.txt.lz4
a => literal 3 
a => literal 4 
a => literal 5 
Last sequence stops right after literals field.

\x1b\x00\x00\x00QHola \x05\x00SAdios\x06\x00\xa0hola adios'



Hola Hola Adios Adios hola adios

Hola Hola Adios Adios hola adios 

BLOQUE 1 
0x51 = Q => Token 5 = (1 hi ha un match tamany 5)
Hola  => literal 
0x05 => offset (0005)
0x00 => offset 

BLOQUE 2 
0x53 = S => token 5 (MATCH LENGTH 2 + 4 = 7) 
Adios => literal 
0x06 offset
0x00

BLOQUE 3 ULTIMO 
0a0 => match length =  
hola adios 

Bua bua bua casa casa bua bua 

SBua b\x04\x003cas\x05\x00\x80bua bua 
B1 
S = 53 
Bua b = literal match loength = 7 
0x04 
0x00 

B2 
3 = 0x33 token match length = 7 
cas
0x05
0x00 

B3
0x80 => token 
bua bua 

[b1, b2, b3]
it ++
push ()

Bua bua bua casa casa 


Note that the last sequence stops right after literals field.

In [81]:
MINIMUM_LENGTH = 4
GOOD_ENOUGH_SIZE = 512
MAX_OFFSET = 65535 # 2 BYTES = 65535
LOOKAHEAD_SIZE= 512

In [38]:


def lsic(length):
    blocks = bytearray()
    count = int(length / 255) # how many 255 we have 
    blocks += b"\xff" * count 
    # add last block 
    blocks.append(int(length % 255)) # append final byte 
    
    return blocks

def createBlock(blocks, literal, match_length, offset, last_block=False):
    # literal = bytes(literal, 'utf-8')
    literal_length = len(literal)
    # codify token 
    token = 0
    match_length -= 4
    if match_length < 15:
        token += match_length 
    else:
        token += 15 
    if last_block:
        token = 0
    if literal_length < 15:
        token += literal_length << 4 
    else:
        token += 15 << 4

    blocks.append(token)
    if literal_length >= 15:
        blocks += lsic(literal_length - 15)
    blocks += literal 
    if not last_block:
        blocks += offset.to_bytes(2, 'little')
    if match_length >= 15:
        blocks += lsic(match_length - 15)

In [76]:
class LinkedHashTable:

    MAX_TABLE_SIZE = 8000000
    
    def __init__(self):
        self.table = collections.OrderedDict()
        
    def find(self, literal):
        if literal in self.table:
            value = self.table[literal]
            self.table.move_to_end(literal)
            return value
        else:
            return None 
        
    
    def add(self, literal, index):
        if literal in self.table:
            self.table[literal].append(index)
        else:
            self.table[literal] = [index]
        self.table.move_to_end(literal)
        if len(self.table) > LinkedHashTable.MAX_TABLE_SIZE:
            self.table.popitem(last = False)
            print("full")

class LZ4:

    ENCODE_EXT = '.lz4'
    DECODE_EXT = '_decoded'

    MIN_MATCH_LENGTH = 4
    
    MINIMUM_LENGTH = 4
    GOOD_ENOUGH_SIZE = 512
    MAX_OFFSET = 65535 # 2 BYTES = 65535

    def __init__(self):
        self.literalLength = 0
        self.matchLength = 0
        self.offset = 0
        self.it = 0
        self.table = LinkedHashTable()
        
    def find_best(self, text, literal):
        match_indices = self.table.find(literal)
        best_match_length = LZ4.MINIMUM_LENGTH - 1
        best_offset = -1 
        match_found = False 
        if match_indices is not None:
            for index in reversed(match_indices):
                match_length, offset = self.iterate(text, index, self.it)
                if match_length > best_match_length:
                    match_found = True
                    best_match_length = match_length 
                    best_offset = offset
                #if best_match_length >= GOOD_ENOUGH_SIZE:
                #    break 
    
        return match_found, best_match_length, best_offset

    def iterate(self, text, match_index, literal_index):
        match_length = LZ4.MINIMUM_LENGTH
        offset = literal_index - match_index 
        if offset > LZ4.MAX_OFFSET:
            return 0, 0
        k = match_index + LZ4.MINIMUM_LENGTH
        j = literal_index + LZ4.MINIMUM_LENGTH
        # search buffer 
        while j < len(text) and text[j] == text[k]:
            j += 1 
            k += 1
            match_length += 1 

        return match_length, offset

    def compress(self, text):
        self.it = 0
        blocks = bytearray()
        last_match = 0
        with tqdm(total=len(text)) as pbar:
            while self.it < len(text):
                #print('=================================')
                #print('Search ', chr(text[i]))
                #print('Text:', text[i:])
                #print('Search buffer:', "".join([chr(i)for i in searchBuffer]))
                #print('Code:', blocks)
                literal = text[self.it:self.it + LZ4.MINIMUM_LENGTH]
                match_found, match_length, offset = self.find_best(text, literal)

                if match_found: # match found

                    # print('Match found with length', match_length, 'and offset', offset)
                    createBlock(blocks, text[last_match:self.it], match_length, offset) 
                    self.table.add(literal, self.it) # remove line to increase speed
                    # remove for increased speed, but less compression
                    for blockByte in range(i, match_length + i, MINIMUM_LENGTH):
                        table.add(text[blockByte:blockByte + MINIMUM_LENGTH], blockByte)
                    self.it += match_length 
                    pbar.update(match_length)
                    last_match = self.it
                else:
                    self.table.add(literal, self.it)
                    pbar.update(1)
                    self.it += 1

        createBlock(blocks, text[last_match:self.it], 0, 0, last_block=True) 
        return blocks

    def readToken(self, code):
        self.literalLength = code[self.it] >> 4 # 4 highest bits
        self.matchLength = code[self.it] & 0x0F # 4 lowest bits 
        
        self.it += 1

    def readLiteral(self, code):
        literal = code[self.it:self.it + self.literalLength]
        self.it += self.literalLength
        #print('Literal found:', literal)
        return literal

    def readLiteralLenght(self, code):
        self.literalLength = self.readLSIC(code, self.literalLength)
        #print('Literal length:', self.literalLength)
        

    def readMatchLength(self, code):
        self.matchLength = self.readLSIC(code, self.matchLength) + LZ4.MIN_MATCH_LENGTH
        #print('Match length:', self.matchLength)

    def readOffset(self, code):
        higher = code[self.it + 1]
        lower = code[self.it]
        #print('Offset hex:', code[self.it:self.it + 1])
        self.offset = (higher << 8) + lower
        self.it += 2
        #print('Offset:', self.offset)

    def readLSIC(self, code, initialLength):
        length = initialLength
        currentByte = initialLength
        # 15 == 4 bits
        if currentByte >= 15:
            currentByte = code[self.it]
            # 8 bits
            while currentByte >= 255:
                length += currentByte
                self.it += 1
                currentByte = code[self.it]
            
            length += currentByte
            self.it += 1 # next block

        return length

    def readMatch(self, text):
        #print('Text Length:', len(text))
        #print('Offset:', self.offset)
        pos = len(text) - self.offset
        for i in range(self.matchLength):
            text.append(text[pos + i]) 


    def decompress(self, code):
        self.it = 0
        text = bytearray()
        with tqdm(total=len(code)) as pbar:
            it_old = self.it 
            while self.it < len(code):
                
                pbar.update(self.it - it_old)
                it_old = self.it
                self.readToken(code)
                #print('It:', self.it)
                self.readLiteralLenght(code)
                #print('It:', self.it)
                literal = self.readLiteral(code)
                #print('It:', self.it)
                text += literal
                if self.it < len(code): # in case it is the last token
                    self.readOffset(code)
                    #print('It:', self.it)
                    self.readMatchLength(code)
                    #print('It:', self.it)
                    # add
                    self.readMatch(text)
                    #print('It:', self.it)
                # print(offsets[k], "==", self.offset)
                #print('Block:', code[it_old:self.it])
                #print('Text:', text)


        return text


In [77]:
file_index = 2
text = open(test_files[file_index], 'rb').read()
lz4 = LZ4()
blocks = lz4.compress(text)
print('Equal:', lz4.decompress(blocks) == text)
print('Ratio:', len(text) / len(blocks))

100%|█████████▉| 453915/453916 [00:00<00:00, 1089137.78it/s]

Equal: True
Ratio: 3.4290044854113977


In [88]:
from tqdm import tqdm 
import collections




text = "Hola Hola Adios Adios hola adios"
text = 'Bua bua bua casa casa bua bua '
text = "La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicada con fecha de 1605, aunque impresa en diciembre de 1604, momento en que ya debió poder leerse en Valladolid"
text = bytes(text, 'utf-8')
#text = open('article.pdf', 'rb').read()
file_index = 
text = open(test_files[file_index], 'rb').read()
print('Test file:', test_files[file_index])

class LinkedHashTable:
    
    MAX_TABLE_SIZE = 800000
    
    def __init__(self):
        self.table = collections.OrderedDict()
        
    def find(self, literal):
        if literal in self.table:
            value = self.table[literal]
            self.table.move_to_end(literal)
            return value
        else:
            return None 
        
    
    def add(self, literal, index):
        if literal in self.table:
            self.table[literal].append(index)
        else:
            self.table[literal] = [index]
        self.table.move_to_end(literal)
        if len(self.table) > LinkedHashTable.MAX_TABLE_SIZE:
            self.table.popitem(last = False)
            print("full")
            

table = LinkedHashTable()

def find_best(literal):
    match_indices = table.find(literal)
    best_match_length = MINIMUM_LENGTH - 1
    best_offset = -1 
    match_found = False 
    if match_indices is not None:
        for index in reversed(match_indices):
            match_length, offset = iterate(index, i)
            if match_length > best_match_length:
                match_found = True
                best_match_length = match_length 
                best_offset = offset
    
    return match_found, best_match_length, best_offset

def iterate(match_index, literal_index):
    match_length = 4
    offset = literal_index - match_index 
    if offset > 65535:
        return 0, 0
    k = match_index + 4
    j = literal_index + 4
    # search buffer 
    while j < len(text) and text[j] == text[k]:
        j += 1 
        k += 1
        match_length += 1 
        
    return match_length, offset
    
i = 0
blocks = bytearray()
last_match = 0
with tqdm(total=len(text)) as pbar:
    while i < len(text):
        #print('=================================')
        #print('Search ', chr(text[i]))
        #print('Text:', text[i:])
        #print('Search buffer:', "".join([chr(i)for i in searchBuffer]))
        #print('Code:', blocks)
        literal = text[i:i + 4]
        match_found, match_length, offset = find_best(literal)
        
        if match_found: # match found

            # print('Match found with length', match_length, 'and offset', offset)
            createBlock(blocks, text[last_match:i], match_length, offset) 
            table.add(literal, i) # remove line to increase speed
            # remove for increased speed, but less compression
            for blockByte in range(i, match_length + i, 1):
                table.add(text[blockByte:blockByte + 4], blockByte)
            i += match_length 
            pbar.update(match_length)
            last_match = i 
        else:
            table.add(literal, i)
            pbar.update(1)
            i += 1
            

createBlock(blocks, text[last_match:i], 0, 0, last_block=True) 

#print("Initial text:", text)
# print("Compressed blocks:", blocks)
print('Ratio:', len(text) / len(blocks))

 23%|██▎       | 67966/298966 [00:00<00:00, 679613.66it/s]

Test file: test_files/wells_the_invisible_man.txt


100%|██████████| 298966/298966 [00:00<00:00, 517175.17it/s]

Ratio: 1.8590678730217953


In [44]:
len(text)

3145782

In [43]:
for i in range(0, len(test_files), 2):
    print('Test file reference:', test_files[i])
    print('Test file reference:', test_files[i + 1])
    original = open(test_files[i], 'rb').read()
    compressed = open(test_files[i + 1], 'rb').read()
    print('Ratio:', len(original) / len(compressed))

Test file reference: test_files/YeMi.dna
Test file reference: test_files/YeMi.dna.lz4
Ratio: 1.8182693019468503
Test file reference: test_files/aes.tar
Test file reference: test_files/aes.tar.lz4
Ratio: 3.912592097291944
Test file reference: test_files/file26.bmp
Test file reference: test_files/file26.bmp.lz4
Ratio: 4.295573995911685
Test file reference: test_files/file28.bmp
Test file reference: test_files/file28.bmp.lz4
Ratio: 4.406605345114797
Test file reference: test_files/openssl
Test file reference: test_files/openssl.lz4
Ratio: 2.0424244396004814
Test file reference: test_files/wells_the_invisible_man.txt
Test file reference: test_files/wells_the_invisible_man.txt.lz4
Ratio: 2.1341756790520043


In [35]:
lz4 = LZ4()
t = lz4.decompress(blocks)

100%|█████████▉| 857236/857237 [00:00<00:00, 1052195.38it/s]


In [48]:
k = open('test_files/wells_the_invisible_man.txt.lz4', 'rb').read()

In [7]:
blocks

bytearray(b'\xf0(\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of \x1f\x00\xf2\x0eInvisible Man, by H. G. WellsD\x00Ais e3\x00\xe0is for the useB\x00\xf0\x19anyone anywhere at no cost and with\r\nalm\x11\x00\xf03no restrictions whatsoever.  You may copy it, give it away or\r\nre-u\x00rit unde\x86\x00Pterms\x88\x00\x00\x93\x00\x0e\xe9\x00\xf0\x03License included\r\n\x91\x005 th\xd2\x00por onli\xc3\x004t g"\x01@.net\xfb\x00\x8e\r\nTitle:)\x01\x00\x1e\x00|Author:0\x01\xf2\x10Release Date: October 7, 2004 [}\x01\xf0\r#5230]\r\n[Last updated: May 3*\x00012]L\x00\x0f\xd5\x01\x02\xf22\r\n*** START OF THIS PROJECT GUTENBERG EBOOK THE INVISIBLE MAN ***\xdb\x00\x00\x02\x00\x80Produced\xf7\x01\xa6Andrew Sly \x00\x02B\x02\t#\x02\x01\xfa\x00\xf0\x03 Grotesque Romance\x17\x00\x1dB<\x02\x00\x16\x00\x80CONTENTS\x0c\x00\x11 \x01\x00!I Q\x01astrangU\x00\xc2\'s Arrival\r\n#\x00\xf0\x15I  Mr. Teddy Henfrey\'s first ImpressF\x02\x020\x00#IIT\x00Pthousz\x02\x00\x04\x00\x00\x9a\x02tBottles

In [68]:
blocks[:400]

bytearray(b'\xf0(\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of \x1f\x00\xf2\x0eInvisible Man, by H. G. WellsD\x00Ais e3\x00\xe0is for the useB\x00\xf0\x19anyone anywhere at no cost and with\r\nalm\x11\x00\xf03no restrictions whatsoever.  You may copy it, give it away or\r\nre-u\x00rit unde\x86\x00Pterms\xca\x00\x00\x93\x00\x0e\xe9\x00\xf0\x03License included\r\n\x91\x005 th\xd2\x00por onli\xc3\x004t g"\x01@.net?\x01\x8e\r\nTitle:)\x01\x00]\x01|Author:0\x01\xf2\x10Release Date: October 7, 2004 [}\x01\xf0\r#5230]\r\n[Last updated: May 3*\x00012]')

In [71]:
k[:300]

b'\xf0(\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of \x1f\x00\xf2\x0eInvisible Man, by H. G. WellsD\x00Ais e3\x00\xe0is for the useB\x00`anyone\x07\x00\xf0\x0fwhere at no cost and with\r\nalm\x11\x00\xf03no restrictions whatsoever.  You may copy it, give it away or\r\nre-u\x00rit unde\x86\x00Pterms\xca\x00\x00\x93\x00\x0e\xe9\x00PLicen4\x00\x90ncluded\r\n\x91\x00& t\xd2\x00por onli\xc3\x004t g"\x01@.net?'

In [10]:
open('test_files/wells_the_invisible_man.txt', 'rb').read()

b'\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of The Invisible Man, by H. G. Wells\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at gutenberg.net\r\n\r\n\r\nTitle: The Invisible Man\r\n\r\nAuthor: H. G. Wells\r\n\r\nRelease Date: October 7, 2004 [EBook #5230]\r\n[Last updated: May 3, 2012]\r\n\r\nLanguage: English\r\n\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK THE INVISIBLE MAN ***\r\n\r\n\r\n\r\n\r\nProduced by Andrew Sly\r\n\r\n\r\n\r\n\r\n\r\nThe Invisible Man\r\n\r\nA Grotesque Romance\r\n\r\nBy H. G. Wells\r\n\r\n\r\n\r\nCONTENTS\r\n\r\n      I  The strange Man\'s Arrival\r\n     II  Mr. Teddy Henfrey\'s first Impressions\r\n    III  The thousand and one Bottles\r\n     IV  Mr. Cuss interviews the Stranger\r\n      V  The Burglary at the Vicarage\r\n     VI  T

In [70]:
open('out_test.lz4', 'wb').write(blocks)

160815

In [8]:
from tqdm import tqdm 
import collections


i = 0
BUFFER_SIZE = 512 # maximum possible offset  65536
searchBuffer = collections.deque(maxlen=BUFFER_SIZE)

text = "Hola Hola Adios Adios hola adios"
text = 'Bua bua bua casa casa bua bua '
text = "La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicada con fecha de 1605, aunque impresa en diciembre de 1604, momento en que ya debió poder leerse en Valladolid"
#text = bytes(text, 'utf-8')
text = open('la_regenta', 'rb').read()


MINIMUM_LENGTH = 4 
GOOD_ENOUGH_SIZE = 256 
LOOKAHEAD_SIZE= 512


# This function if the bottlneck of the algorithm
def search(it):
    has_match = False 
    match_length = None 
    offset = 0 
    j = 0
    k = it # save reference
    best_match_length = MINIMUM_LENGTH - 1
    lookahead_length = min(LOOKAHEAD_SIZE, len(text))
    best_offset = -1 
    searchBufferIterator = 0
     

    for searchBufferIterator in range(len(searchBuffer)): # loops BUFFER_SIZE times
        # print(searchBuffer[j], '==', text[it]
        j = searchBufferIterator
        if searchBuffer[j] == text[it]:
            # print('Coincidence:', chr(searchBuffer[j]), '==', chr(text[it]))
            
            match_length = 0
            offset = len(searchBuffer) - searchBufferIterator
            # search buffer 
            while j < len(searchBuffer) and it < len(text) and searchBuffer[j] == text[it]:
                j += 1 
                it += 1
                match_length += 1 
                
            # lookahead 
            if j >= len(searchBuffer):
                itBegin = k 
                while it < lookahead_length and text[it] == text[itBegin]: 
                    itBegin += 1 
                    it += 1 
                    match_length += 1
            
            # print('Match of size', match_length)
            if match_length > best_match_length:
                best_match_length = match_length 
                best_offset = offset 
                # print('Initial pos:', searchBufferIterator)
                has_match = True  
                break
            if best_match_length >= GOOD_ENOUGH_SIZE:
                break 
            
                
        it = k 

            
            
    return has_match, best_match_length, best_offset


    

blocks = bytearray()
last_match = 0
with tqdm(total=len(text)) as pbar:
    while i < len(text):
        # print('=================================')
        # print('Search ', chr(text[i]))
        # print('Text:', text[i:])
        # print('Search buffer:', "".join([chr(i)for i in searchBuffer]))
        # print('Code:', blocks)
        
        has_match, match_length, offset = search(i)
        if has_match:
            # print('Match found with length', match_length, 'and offset', offset)
            createBlock(blocks, text[last_match:i], match_length, offset)
            # print('Append to buffer:', text[i:i + match_length])
            searchBuffer += text[i:i + match_length]
            i += match_length
            pbar.update(match_length)
            last_match = i
        else:
            # print('Not found')
            searchBuffer.append(text[i]) # add byte to buffer 
            i += 1 # 1 literal 
            pbar.update(1)
        

createBlock(blocks, text[last_match:i], 0, 0, True)
    
print("Initial text:", text)
print("Compressed blocks:", blocks)
print('Ratio:', len(text) / len(blocks))

  3%|▎         | 61283/1841897 [00:02<01:05, 27309.53it/s]


KeyboardInterrupt: 

In [387]:
open('lz4/test.lz4', 'rb').read()

b'\x04"M\x18d@\xa7\xbe\x00\x00\x00\xf01La novela consta de dos partes: El ingenioso hidalgo don Quijote0\x00\xf1\x04la Mancha, publicadO\x00Q fechR\x00\xf1\x111605, aunque impresa en diciembrG\x00\xd01604, momento\x1e\x00\x00-\x00\x10y@\x00\xf0\x02bi\xc3\xb3 poder leerse\x1e\x00\xa0Valladolid\x00\x00\x00\x00\x9c\xd9\x8f\xc3'

In [421]:
x = "La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicad"
x[-75]

'n'

In [416]:
lz4 = LZ4()
lz4.decompress(open('lz4/test.lz4', 'rb').read()[11:-8]).decode()

 94%|█████████▍| 179/190 [00:00<00:00, 1930026.78it/s]


'La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicada con fecha de 1605, aunque impresa en diciembre de 1604, momento en que ya debió poder leerse en Valladolid'

In [31]:
lz4 = LZ4()
lz4.decompress(blocks).decode()

100%|█████████▉| 857236/857237 [00:00<00:00, 1033200.97it/s]


UnicodeDecodeError: 'utf-8' codec can't decode byte 0x90 in position 187443: invalid start byte

b'QHola \x05\x00SAdios\x06\x00\xa0hola adios'

QHola \x05\x00RAdios\x06\x00\xac hola adios

token = 51 = 5 
literal = Hola 
Offset = 5 
token = 52 = 6 
literal = Adios
offset = 6 

Hola Hola Adios Adios hola adios 






In [3]:
from tqdm import tqdm 

with tqdm(total=100) as pbar:
    i = 0 
    while i < 100:
        pbar.update(1)

25715061it [00:09, 2703972.72it/s]     


KeyboardInterrupt: 

In [35]:
print(text)
print(blocks)
lz4 = LZ4()
lz4.decompress(blocks)

La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicada con fecha de 1605, aunque impresa en diciembre de 1604, momento en que ya debió poder leerse en Valladolid
b'\xf01La novela consta de dos partes: El ingenioso hidalgo don Quijote0\x00\xf1\x04la Mancha, publicadO\x00Q fechR\x00\xf1\x111605, aunque impresa en diciembrG\x00\xd01604, momento\x1e\x00\x00-\x00\x10y\x92\x00\xf0\x02bi\xc3\xb3 poder leerse;\x00\xa0Valladolid'
It: 1
Literal length: 64
It: 2
Literal found: La novela consta de dos partes: El ingenioso hidalgo don Quijote
It: 66
Offset: 48
It: 68
Match length: 4
It: 68
It: 68
Text: La novela consta de dos partes: El ingenioso hidalgo don Quijote de 
It: 69
Literal length: 19
It: 70
Literal found: la Mancha, publicad
It: 89
Offset: 79
It: 91
Match length: 5
It: 91
It: 91
Text: La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicada con
It: 92
Literal length: 5
It: 92
Literal found:  fech
It: 97
Offset: 82
It: 99


'La novela consta de dos partes: El ingenioso hidalgo don Quijote de la Mancha, publicada con fecha de 1605, aunque impresa en diciembre de 1604, momento en que ya debió poder leerse en Valladolid'

In [29]:
blocks

b'/\n \x01\x00\x12\xbfLa Regenta\n2\x00\x0e\xff\nLeopoldo Alas \xc2\xabClar\xc3\xadn\xc2\xbb8\x00\x0f\x04\x8a\x00S- I -g\x00\xf0(La heroica ciudad dorm\xc3\xada la siesta. El viento Sur, cal\x0e\x00\xf0\x08e y perezoso, empujaba\n\x93\x00\xf01nubes blanquecinas que se rasgaban al correr hacia el Norte. En \xd7\x00\xf1\x0ccalles no\nhab\xc3\xada m\xc3\xa1s ruidoK\x00\xf1el rumor estrid\x8f\x00\xf0\x01de los remolinos\x11\x00\xf0\x0cpolvo, trapos, pajas y\npape^\x00\x00\x96\x00\x10i\x8f\x00\xc3de arroyo en\n\x00\x11,\x15\x00Acera\x14\x00\x00\t\x00\x01\x13\x00aesquin\x15\x00\x03\x0b\x00\xa2\nrevolando\x13\x01\xf6\x0bsigui\xc3\xa9ndose, como maripos\x08\x01\xd0buscan y huye\x08\x00\x03\xd5\x00\xd0aire\nenvuelve\x8c\x00\xf2\x14sus pliegues invisibles. Cual turba\xe9\x00`illuel\xe5\x00Paquel\x87\x011mig\xf0\x00\x00\x19\x01`a\nbasu\xc3\x00\x05\x1f\x00Bsobr=\x00@todo\x9e\x01Ajunt\x9e\x01\xd0en un mont\xc3\xb3n6\x01\x82r\xc3\xa1banse\xcd\x00\xf0\x03dormidas un\nmoment\xf8\x00Qbrinc\xdb\x01\x81d

In [15]:
class LZ4:

    ENCODE_EXT = '.lz4'
    DECODE_EXT = '_decoded'

    MIN_MATCH_LENGTH = 4

    def __init__(self):
        self.literalLength = 0
        self.matchLength = 0
        self.offset = 0
        self.it = 0

    def compress(self, text):

        return text

    def readToken(self, code):
        self.literalLength = code[self.it] >> 4 # 4 highest bits
        self.matchLength = code[self.it] & 0x0F # 4 lowest bits 
        
        self.it += 1

    def readLiteral(self, code):
        literal = code[self.it:self.it + self.literalLength]
        self.it += self.literalLength
        print('Literal found:', literal)
        return literal

    def readLiteralLenght(self, code):
        self.literalLength = self.readLSIC(code, self.literalLength)
        print('Literal length:', self.literalLength)
        

    def readMatchLength(self, code):
        self.matchLength = self.readLSIC(code, self.matchLength) + LZ4.MIN_MATCH_LENGTH
        print('Match length:', self.matchLength)

    def readOffset(self, code):
        higher = code[self.it + 1]
        lower = code[self.it]
        print('Offset hex:', code[self.it:self.it + 1])
        self.offset = (higher << 8) + lower
        self.it += 2
        print('Offset:', self.offset)

    def readLSIC(self, code, initialLength):
        length = initialLength
        currentByte = initialLength
        # 15 == 4 bits
        if currentByte >= 15:
            currentByte = code[self.it]
            # 8 bits
            while currentByte >= 255:
                length += currentByte
                self.it += 1
                currentByte = code[self.it]
            
            length += currentByte
            self.it += 1 # next block

        return length

    def readMatch(self, text):
        print('Text Length:', len(text))
        print('Offset:', self.offset)
        pos = len(text) - self.offset
        for i in range(self.matchLength):
            text.append(text[pos + i]) 


    def decompress(self, code):
        self.it = 0
        text = bytearray()
        with tqdm(total=len(code)) as pbar:
            it_old = self.it 
            while self.it < len(code):
                
                pbar.update(self.it - it_old)
                it_old = self.it
                self.readToken(code)
                #print('It:', self.it)
                self.readLiteralLenght(code)
                #print('It:', self.it)
                literal = self.readLiteral(code)
                #print('It:', self.it)
                text += literal
                if self.it < len(code): # in case it is the last token
                    self.readOffset(code)
                    #print('It:', self.it)
                    self.readMatchLength(code)
                    #print('It:', self.it)
                    # add
                    self.readMatch(text)
                    #print('It:', self.it)
                # print(offsets[k], "==", self.offset)
                #print('Block:', code[it_old:self.it])
                #print('Text:', text)


        return text


In [18]:
lz4 = LZ4()
t = open('test_files/wells_the_invisible_man.txt', 'rb').read()
d = lz4.decompress(blocks)

  1%|          | 1331/155042 [00:00<00:14, 10552.56it/s]

Literal length: 55
Literal found: bytearray(b'\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of ')
Offset hex: bytearray(b'\x1f')
Offset: 31
Match length: 4
Text Length: 55
Offset: 31
Block: bytearray(b'\xf0(\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of \x1f\x00')
Text: bytearray(b'\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of The ')
Literal length: 29
Literal found: bytearray(b'Invisible Man, by H. G. Wells')
Offset hex: bytearray(b'D')
Offset: 68
Match length: 6
Text Length: 88
Offset: 68
Block: bytearray(b'\xf2\x0eInvisible Man, by H. G. WellsD\x00')
Text: bytearray(b'\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of The Invisible Man, by H. G. Wells\r\n\r\nTh')
Literal length: 4
Literal found: bytearray(b'is e')
Offset hex: bytearray(b'3')
Offset: 51
Match length: 5
Text Length: 98
Offset: 51
Block: bytearray(b'Ais e3\x00')
Text: bytearray(b'\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBo

  2%|▏         | 2390/155042 [00:00<00:15, 10137.81it/s]

2863
Offset: 1640
Block: bytearray(b'Pwho\r\nh\x06')
Text: bytearray(b'\xef\xbb\xbfLanguage: English\r\n\r\nThe Project Gutenberg EBook of The Invisible Man, by H. G. Wells\r\n\r\nThis eBook is for the use of anyone anywhere at no cost and with\r\nalmost no restrictions whatsoever.  You may copy it, give it away or\r\nre-use it under the terms of the Project Gutenberg License included\r\nwith this eBook or online at gutenberg.net\r\n\r\n\r\nTitle: The Invisible Man\r\n\r\nAuthor: H. G. Wells\r\n\r\nRelease Date: October 7, 2004 [EBook #5230]\r\n[Last updated: May 3, 2012]\r\n\r\nLanguage: English\r\n\r\n\r\n*** START OF THIS PROJECT GUTENBERG EBOOK THE INVISIBLE MAN ***\r\n\r\n\r\n\r\n\r\nProduced by Andrew Sly\r\n\r\n\r\n\r\n\r\n\r\nThe Invisible Man\r\n\r\nA Grotesque Romance\r\n\r\nBy H. G. Wells\r\n\r\n\r\n\r\nCONTENTS\r\n\r\n      I  The strange Man\'s Arrival\r\n     II  Mr. Teddy Henfrey\'s first Impressions\r\n    III  The thousand and one Bottles\r\n     IV  Mr. Cuss interview

  3%|▎         | 4216/155042 [00:00<00:24, 6181.49it/s] 

...

 67%|██████▋   | 104505/155042 [01:04<00:40, 1234.40it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 68%|██████▊   | 104879/155042 [01:05<00:46, 1068.51it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 68%|██████▊   | 105445/155042 [01:05<00:43, 1138.66it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable

 75%|███████▍  | 115802/155042 [01:16<00:34, 1125.34it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 75%|███████▌  | 116309/155042 [01:17<00:34, 1125.63it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 75%|███████▌  | 116842/155042 [01:17<00:35, 1072.20it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable

 82%|████████▏ | 127018/155042 [01:29<00:25, 1108.61it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 82%|████████▏ | 127523/155042 [01:29<00:24, 1108.02it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 83%|████████▎ | 128025/155042 [01:30<00:25, 1074.42it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable

 89%|████████▉ | 137706/155042 [01:41<00:17, 1002.52it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 89%|████████▉ | 138186/155042 [01:42<00:16, 1020.75it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 89%|████████▉ | 138672/155042 [01:43<00:16, 1013.92it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable

 96%|█████████▌| 148533/155042 [01:55<00:06, 962.40it/s] IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 96%|█████████▌| 149002/155042 [01:55<00:06, 969.62it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 96%|█████████▋| 149489/155042 [01:56<00:05, 970.18it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`

In [392]:
d.decode() == open('la_regenta.lz4', 'rb').read()

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xe1 in position 2: invalid continuation byte

In [298]:
lz4 = LZ4()
d2 = lz4.decompress(blocks)

  0%|          | 253/1650044 [00:00<00:01, 1533466.64it/s]


IndexError: bytearray index out of range

In [498]:
open('regenta2', 'rb').read().decode('utf-8')

UnicodeDecodeError: 'utf-8' codec can't decode byte 0xe1 in position 2: invalid continuation byte

In [226]:
t

b'/\n \x01\x00\x12\xbfLa Regenta\n2\x00\x0e\xff\nLeopoldo Alas \xc2\xabClar\xc3\xadn\xc2\xbb;\x00\x0f\x04\x02\x00S- I -/\x00\xf2\xff\x1cLa heroica ciudad dorm\xc3\xada la siesta. El viento Sur, caliente y perezoso, empujaba\nlas nubes blanquecinas que se rasgaban al correr hacia el Norte. En las calles no\nhab\xc3\xada m\xc3\xa1s ruido que el rumor estridente de los remolinos de polvo, trapos, pajas y\npapeles que iban de arroyo en arroyo, de acera en\t\x00\xf4\x00, de esquina en\x0b\x00\xa2\nrevolando\x15\x01\xf6\x0bsigui\xc3\xa9ndose, como maripos\x0b\x01\xf1\x01buscan y huyen y#\x01\xf2(el aire\nenvuelve en sus pliegues invisibles. Cual turba\xea\x00\xf1\x07illuelos, aquellas mig\xf1\x00\xc7de la\nbasura\x1f\x00Bsobr=\x00\xc1todo se junt\xa1\x01\xf2\nen un mont\xc3\xb3n, par\xc3\xa1banse\xcf\x00\xf1\x00dormidas un\nmom\x1e\x02\x83y brincaO\x01\xf3\x0fnuevo sobresaltadas, dispers\xc3\xa1\x1c\x01Atrep8\x01\xf2$unas por las\nparedes hasta los cristales tembloroso\xd7\x00\xf9\x01os faro

In [391]:
k = open('la_regenta', 'rb').read()

In [273]:
k.decode('utf-8') == d.decode()

True

In [344]:
from lz77 import LZ77Compressor

cmp = LZ77Compressor()
cmp.compress('regenta2')

NameError: name 'bitarray' is not defined